# Sea Level: Tidal Data 
Notebook for analysing tide measurement data for 1490 tide gauges worldwide. I use the Revised Local Reference (RLR) data set from Permanent Service of Mean Sea Level . The RLR datum is set to 7000 mm below mean sea level therefore the values are all in the range of 6000 to 8000 mm.

All UK tide gauge data is included in the PSMSL data set, most of the data from the University of Hawaii is included as well.

Data source is Permanent Service of Mean Sea Level (http://www.psmsl.org/data/obtaining/complete.php, RLR monthly)

Data set with monthly mean data.

Data has been obtained on 10 February 2017.

## Load libraries

In [2]:
%matplotlib inline

from IPython.core.interactiveshell import InteractiveShell
from datetime import datetime

#get data from worldbank
from pandas_datareader import wb

import glob
import os
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib
import json
import matplotlib.pyplot as plt

#create leaflet maps
import folium

InteractiveShell.ast_node_interactivity = "all"
pd.options.display.max_rows = 200
#matplotlib.rcParams['svg.fonttype'] = 'none'


## Setup the data
### First: Read meta data for all stations of PSMSL

In [3]:
#parse errorflags
stations_errorflag = 'data/psmsl_data/filelist.txt'

errors = pd.read_csv(stations_errorflag, sep=';', header=None, usecols=[0, 6], names=['id', 'latitude', 'longitude', 'locataion', 'coastline', 'station', 'flag' ])

#parse meta data
meta_info = 'data/metadata_psmsl.csv'

stations = pd.read_csv(meta_info, header=0, names=['location', 'ID', 'latitude', 'longitude', 'gloss id', 'country', 'date', 'coastline', 'station'])

#comibe meta data and error flags
stations = stations.merge(errors, left_on='ID', right_on='id')

stations = stations.drop('ID', 1)

len(errors)
len(stations)

stations.head()

1490

1490

location  latitude  longitude  gloss id country  \
0                     REYKJAVIK    64.151    -21.940     229.0     ISL   
1                     GRINDAVIK    63.833    -22.433       NaN     ISL   
2                      TORSHAVN    62.017     -6.767     237.0     FRO   
3                   BARENTSBURG    78.067     14.250     231.0     SJM   
4  BARENTSBURG II (SPITSBERGEN)    78.067     14.250     231.0     SJM   

         date  coastline  station   id flag  
0  24/01/2017         10        1  638    N  
1  01/01/1980         10       11  877    N  
2  30/10/2007         15       11  839    N  
3  17/01/2017         25        1  541    N  
4  17/01/2003         25        2  547    N

In [4]:
#convert capitals to lowercase with a capitalized first letter
def convert_location_names(str):
    conversion = str.title()
    return conversion

stations['location'] = stations['location'].apply(convert_location_names)


### Second: Read all the tide data from folder

In [6]:
#parse file

def parse_tides(filename):
    filepath = 'data/psmsl_data/' + str(filename) + '.rlrdata'
    df = pd.read_csv(filepath, sep=';', header=None, names=['year-month', 'tide', 'missing day', 'flag for attention'])

    df['flag for attention'] = df['flag for attention'].apply(lambda x: '{0:0>3}'.format(x))
    df['year'] = df['year-month'].apply(np.floor).astype('int')
    df['month'] = ((((df['year-month'] - df['year'])*24)+1)/2).apply(np.around).astype('int')
    df['day'] = 1 #due the monthly averages, no days are present, set days to 1
    df['timestamp'] = pd.to_datetime(df[['year', 'month', 'day']], errors='coerce')
    df['ID'] = filename
    df['ID'] = df['ID'].astype('int')

    df = df.drop('year-month', 1)
    df = df.drop('year', 1)
    df = df.drop('month', 1)
    df = df.drop('day', 1)
    
    #print (filepath)
    
    return df

#filepath for complete tide data set
filepath = 'data/psmsl_data/tideData_psmsl_complete.csv'

if os.path.exists(filepath):
    df = pd.read_csv(filepath, usecols=[1,2,3,4,5])
    df['flag for attention'] = df['flag for attention'].apply(lambda x: '{0:0>3}'.format(x))
    df['timestamp'] = pd.to_datetime(df['timestamp'], errors='coerce')
else:
    df = pd.concat([parse_tides(f) for f in stations['id']])
    #replace null values
    df['tide'] = df['tide'].replace("-99999",np.nan)
    df.to_csv(filepath)

df['ID'].nunique()
df.head()

1490

tide  missing day flag for attention  timestamp   ID
0  6980.0            0                000 1956-05-01  638
1  6840.0            0                000 1956-06-01  638
2  6890.0            0                000 1956-07-01  638
3  6830.0            0                000 1956-08-01  638
4  6830.0            0                000 1956-09-01  638

### Third: Merge meta data and tide data

In [7]:
df = df.merge(stations, left_on='ID', right_on='id')

df = df.drop('id', 1)

df['ID'].nunique()
df.head()


1490

tide  missing day flag for attention  timestamp   ID   location  \
0  6980.0            0                000 1956-05-01  638  Reykjavik   
1  6840.0            0                000 1956-06-01  638  Reykjavik   
2  6890.0            0                000 1956-07-01  638  Reykjavik   
3  6830.0            0                000 1956-08-01  638  Reykjavik   
4  6830.0            0                000 1956-09-01  638  Reykjavik   

   latitude  longitude  gloss id country        date  coastline  station flag  
0    64.151     -21.94     229.0     ISL  24/01/2017         10        1    N  
1    64.151     -21.94     229.0     ISL  24/01/2017         10        1    N  
2    64.151     -21.94     229.0     ISL  24/01/2017         10        1    N  
3    64.151     -21.94     229.0     ISL  24/01/2017         10        1    N  
4    64.151     -21.94     229.0     ISL  24/01/2017         10        1    N

In [8]:
len(df)

703599

In [9]:
df.to_csv('psmsl_data_complete_including_metadata.csv')

## Add continent data

In [11]:
continents = pd.read_csv('continents.csv')

df_continents = continents.merge(df, left_on='iso3', right_on='country')

df_continents

continent iso3    tide  missing day flag for attention  timestamp  \
0       Antarctica  ATA  7170.0            0                000 1961-02-01   
1       Antarctica  ATA     NaN            0                000 1961-03-01   
2       Antarctica  ATA     NaN            0                000 1961-04-01   
3       Antarctica  ATA  7202.0            0                000 1961-05-01   
4       Antarctica  ATA     NaN            0                000 1961-06-01   
5       Antarctica  ATA     NaN            0                000 1961-07-01   
6       Antarctica  ATA     NaN            0                000 1961-08-01   
7       Antarctica  ATA     NaN            0                000 1961-09-01   
8       Antarctica  ATA     NaN            0                000 1961-10-01   
9       Antarctica  ATA     NaN            0                000 1961-11-01   
10      Antarctica  ATA     NaN            0                000 1961-12-01   
11      Antarctica  ATA  7117.0            0                000 1962-01-01   
12      Antarctica  ATA  7175.0            0                000 1962-02-01   
13      Antarctica  ATA  7100.0            0                000 1962-03-01   
14      Antarctica  ATA  7033.0            0                000 1962-04-01   
15      Antarctica  ATA  7112.0            0                000 1962-05-01   
16      Antarctica  ATA  7268.0            0                000 1962-06-01   
17      Antarctica  ATA     NaN            0                000 1962-07-01   
18      Antarctica  ATA  7101.0            0                000 1962-08-01   
19      Antarctica  ATA  7160.0            0                000 1962-09-01   
20      Antarctica  ATA  7085.0            0                000 1962-10-01   
21      Antarctica  ATA  7121.0            0                000 1962-11-01   
22      Antarctica  ATA  7164.0            0                000 1962-12-01   
23      Antarctica  ATA     NaN            0                000 1963-01-01   
24      Antarctica  ATA     NaN            0                000 1963-02-01   
25      Antarctica  ATA     NaN            0                000 1963-03-01   
26      Antarctica  ATA     NaN            0                000 1963-04-01   
27      Antarctica  ATA     NaN            0                000 1963-05-01   
28      Antarctica  ATA     NaN            0                000 1963-06-01   
29      Antarctica  ATA     NaN            0                000 1963-07-01   
30      Antarctica  ATA     NaN            0                000 1963-08-01   
31      Antarctica  ATA     NaN            0                000 1963-09-01   
32      Antarctica  ATA     NaN            0                000 1963-10-01   
33      Antarctica  ATA     NaN            0                000 1963-11-01   
34      Antarctica  ATA     NaN            0                000 1963-12-01   
35      Antarctica  ATA  7147.0            0                000 1964-01-01   
36      Antarctica  ATA  7236.0            0                000 1964-02-01   
37      Antarctica  ATA  7168.0            0                000 1964-03-01   
38      Antarctica  ATA  7193.0            0                000 1964-04-01   
39      Antarctica  ATA  7186.0            0                000 1964-05-01   
40      Antarctica  ATA     NaN            0                000 1964-06-01   
41      Antarctica  ATA     NaN            0                000 1964-07-01   
42      Antarctica  ATA     NaN            0                000 1964-08-01   
43      Antarctica  ATA     NaN            0                000 1964-09-01   
44      Antarctica  ATA     NaN            0                000 1964-10-01   
45      Antarctica  ATA     NaN            0                000 1964-11-01   
46      Antarctica  ATA     NaN            0                000 1964-12-01   
47      Antarctica  ATA  7175.0            0                000 1965-01-01   
48      Antarctica  ATA  7082.0            0                000 1965-02-01   
49      Antarctica  ATA  7118.0            0                000 1965-03-01   
50      Antarctica  ATA  7141.0

### Filter data by quality flags

Data flagged for attention: 001 means data should be treated with caution, 010 indicates a mean tidal level (MTL) value in a mean sea level (MSL) time series

In [12]:
df.flag = df.flag.str.strip()

df['missing day'] = df['missing day'].replace("99",np.nan)

data_flagged = df[(df['flag for attention'] == '011')]

#data_flagged.sort_values('missing day', ascending=False)

data_without_flag = df[df['flag for attention'].isin(['001', '011']) == False]
#data_without_flag = df[df['flag for attention'].isin(['011']) == False]

#data_without_flag.sort_values('flag for attention')

data_without_flag.shape
df.shape

#89 Location sind geflaggt mit 001 und eine Location mit 011, gesamte Anzahl Locations 1478


(701692, 14)

(703599, 14)

In [13]:
df = data_without_flag

In [14]:
data_flagged = df[(df['flag for attention'] == '011')]
data_flagged

Empty DataFrame
Columns: [tide, missing day, flag for attention, timestamp, ID, location, latitude, longitude, gloss id, country, date, coastline, station, flag]
Index: []

## Data selction

In [19]:
#function that evaluates how many empty values a station has and start and end of each station

def empty_values(dataframe):
    
    station = dataframe.set_index('timestamp').tide.resample('1A').mean()
    
    first_year = station.first_valid_index().year
    last_year = station.last_valid_index().year
    count_missing = station.isnull().sum()
    count_values = station.count()
    
    
    #tide_first = station.iloc[0]
    #station = station.sort_values(ascending=False)
    #tide_last = station.iloc[0]
    #tide_change = tide_last - tide_first
    
    result = {}

    result['Start'] = first_year
    result['End'] = last_year
    result['Valid Data Points'] = count_values
    result['Missing Data Points'] = count_missing
    
    return pd.Series(result) #create a series


#call function and collect all data
#clean_data = df.groupby(['Location', 'Country']).apply(empty_values).sort_values('Valid Data Points', ascending=False)

#clean_data = df.groupby(['ID']).apply(empty_values).sort_values('Valid Data Points', ascending=False)


#reset index

#clean_data = clean_data.reset_index()


In [17]:
data_subset_1985_2015 = df.set_index(['timestamp'])

data_subset_1985_2015 = data_subset_1985_2015.loc['1985-01-01':'2015-12-01']

data_subset_1985_2015 = data_subset_1985_2015.reset_index()

In [20]:
clean_data = data_subset_1985_2015.groupby(['ID']).apply(empty_values).sort_values('Valid Data Points', ascending=False)

clean_data = clean_data.reset_index()

data_subset_1985_2015_clean = clean_data[(clean_data['Start'] <= 1985)
                               & (clean_data['Valid Data Points'] >= 21) 
                               & (clean_data['End'] >= 2010) ]
data_subset_1985_2015_clean
data_subset_1985_2015_clean['ID'].nunique()

ID   End  Missing Data Points  Start  Valid Data Points
0       1  2015                    0   1985                 31
1    1152  2015                    0   1985                 31
2     518  2015                    0   1985                 31
3     513  2015                    0   1985                 31
4    1237  2015                    0   1985                 31
5     510  2015                    0   1985                 31
6     509  2015                    0   1985                 31
7     508  2015                    0   1985                 31
8    1239  2015                    0   1985                 31
9    1241  2015                    0   1985                 31
10    499  2015                    0   1985                 31
11    498  2015                    0   1985                 31
12    497  2015                    0   1985                 31
13   1242  2015                    0   1985                 31
14   1244  2015                    0   1985                 31
15   1245  2015                    0   1985                 31
16    489  2015                    0   1985                 31
17   1246  2015                    0   1985                 31
18    487  2015                    0   1985                 31
19    486  2015                    0   1985                 31
20    485  2015                    0   1985                 31
21   1236  2015                    0   1985                 31
22    520  2015                    0   1985                 31
23    521  2015                    0   1985                 31
24   1210  2015                    0   1985                 31
25   1153  2015                    0   1985                 31
26   1154  2015                    0   1985                 31
27   1155  2015                    0   1985                 31
28   1157  2015                    0   1985                 31
29   1158  2015                    0   1985                 31
30   1193  2015                    0   1985                 31
31   1209  2015                    0   1985                 31
32    541  2015                    0   1985                 31
33    539  2015                    0   1985                 31
34    522  2015                    0   1985                 31
35    538  2015                    0   1985                 31
36   1211  2015                    0   1985                 31
37   1212  2015                    0   1985                 31
38   1213  2015                    0   1985                 31
39    526  2015                    0   1985                 31
40   1233  2015                    0   1985                 31
41   1234  2015                    0   1985                 31
42    523  2015                    0   1985                 31
43    484  2015                    0   1985                 31
44    483  2015                    0   1985                 31
45   1247  2015                    0   1985                 31
46   1349  2015                    0   1985                 31
47    413  2015                    0   1985                 31
48    412  2015                    0   1985                 31
49   1325  2015                    0   1985                 31
50   1327  2015                    0   1985                 31
51   1328  2015                    0   1985                 31
52    407  2015                    0   1985                 31
53    405  2015                    0   1985                 31
54    757  2015                    0   1985                 31
55    396  2015                    0   1985                 31
56   1322  2015                    0   1985                 31
57    395  2015                    0   1985                 31
58    394  2015                    0   1985                 31
59    393  2015                    0   1985                 31
60    392  2015                    0   1985                 31
61   1351  2015                    0   1985                 31
62   1352  2015                    0  

513

In [22]:
data_subset_1985_2015_clean = data_subset_1985_2015_clean.merge(df, left_on='ID', right_on='ID')

## Export Datasets for Map Visualization

In [23]:
def yearly_mean(dataframe):
    
    mean_dataframe = dataframe.set_index('timestamp').tide.resample('1A').mean()
    mean_dataframe = mean_dataframe.reset_index()
    
    return pd.DataFrame(mean_dataframe)

def rolling_mean(dataframe):
    
    mean_dataframe = dataframe.set_index('timestamp').tide.resample('1A').mean()

    mean_dataframe = mean_dataframe.rolling(center=False, window=5, min_periods=1).mean()
    mean_dataframe = mean_dataframe.reset_index()
    
    
    return pd.DataFrame(mean_dataframe)


normal = df.groupby(['ID']).apply(yearly_mean)

rolling = df.groupby(['ID']).apply(rolling_mean)

normal.head()

rolling.head()

timestamp         tide
ID                          
1  0 1807-12-31  6970.333333
   1 1808-12-31  6867.333333
   2 1809-12-31  6954.916667
   3 1810-12-31  6946.416667
   4 1811-12-31  6977.166667

timestamp         tide
ID                          
1  0 1807-12-31  6970.333333
   1 1808-12-31  6918.833333
   2 1809-12-31  6930.861111
   3 1810-12-31  6934.750000
   4 1811-12-31  6943.233333

In [43]:
#delete rows which are not used for visualization

data_subset_viz = data_subset_1985_2015_clean.drop(['missing day','flag for attention', 'gloss id', 'coastline', 'flag', 'station', 'date'], 1)

data_subset_viz = data_subset_viz.groupby(['ID']).apply(rolling_mean)

data_subset_viz = data_subset_viz.reset_index()

#delete rows which are not used for visualization

data_subset_viz = data_subset_viz.drop(['level_1'], 1)

#filter by trend data
#data_subset_viz = data_subset_viz.merge(trends_1985_2014, left_on='ID', right_on='ID')

#add worldbank data
#data_subset_viz = data_subset_viz.merge(worldbank_data, left_on='ID', right_on='ID')

data_subset_viz = data_subset_viz.round()

data_subset_viz.head()
data_subset_viz['ID'].nunique()

ID  timestamp    tide
0   1 1807-12-31  6970.0
1   1 1808-12-31  6919.0
2   1 1809-12-31  6931.0
3   1 1810-12-31  6935.0
4   1 1811-12-31  6943.0

513

#### Use only for map animation in order to reduce data to 30 years

In [25]:
data_subset_viz = data_subset_viz.set_index(['timestamp'])

data_subset_viz = data_subset_viz.loc['1985-12-31':'2015-12-31']

data_subset_viz = data_subset_viz.reset_index()

#data_subset_viz.sort_values('timestamp', ascending=False)

data_subset_viz['ID'].nunique()

513

#### Add geodata and meta data again

In [44]:
data_subset_viz = data_subset_viz.merge(stations, left_on='ID', right_on='id')

data_subset_viz = data_subset_viz.drop(['gloss id', 'coastline', 'flag', 'station', 'date', 'id'], 1)

data_subset_viz['year'] = data_subset_viz.timestamp.dt.year

data_subset_viz

ID  timestamp    tide                  location  latitude  longitude  \
0         1 1807-12-31  6970.0                     Brest    48.383     -4.495   
1         1 1808-12-31  6919.0                     Brest    48.383     -4.495   
2         1 1809-12-31  6931.0                     Brest    48.383     -4.495   
3         1 1810-12-31  6935.0                     Brest    48.383     -4.495   
4         1 1811-12-31  6943.0                     Brest    48.383     -4.495   
5         1 1812-12-31  6944.0                     Brest    48.383     -4.495   
6         1 1813-12-31  6955.0                     Brest    48.383     -4.495   
7         1 1814-12-31  6953.0                     Brest    48.383     -4.495   
8         1 1815-12-31  6949.0                     Brest    48.383     -4.495   
9         1 1816-12-31  6945.0                     Brest    48.383     -4.495   
10        1 1817-12-31  6939.0                     Brest    48.383     -4.495   
11        1 1818-12-31  6947.0                     Brest    48.383     -4.495   
12        1 1819-12-31  6947.0                     Brest    48.383     -4.495   
13        1 1820-12-31  6944.0                     Brest    48.383     -4.495   
14        1 1821-12-31  6945.0                     Brest    48.383     -4.495   
15        1 1822-12-31  6946.0                     Brest    48.383     -4.495   
16        1 1823-12-31  6943.0                     Brest    48.383     -4.495   
17        1 1824-12-31  6940.0                     Brest    48.383     -4.495   
18        1 1825-12-31  6943.0                     Brest    48.383     -4.495   
19        1 1826-12-31  6930.0                     Brest    48.383     -4.495   
20        1 1827-12-31  6920.0                     Brest    48.383     -4.495   
21        1 1828-12-31  6925.0                     Brest    48.383     -4.495   
22        1 1829-12-31  6926.0                     Brest    48.383     -4.495   
23        1 1830-12-31  6926.0                     Brest    48.383     -4.495   
24        1 1831-12-31  6941.0                     Brest    48.383     -4.495   
25        1 1832-12-31  6941.0                     Brest    48.383     -4.495   
26        1 1833-12-31  6931.0                     Brest    48.383     -4.495   
27        1 1834-12-31  6925.0                     Brest    48.383     -4.495   
28        1 1835-12-31  6920.0                     Brest    48.383     -4.495   
29        1 1836-12-31  6905.0                     Brest    48.383     -4.495   
30        1 1837-12-31  6908.0                     Brest    48.383     -4.495   
31        1 1838-12-31  6899.0                     Brest    48.383     -4.495   
32        1 1839-12-31  6894.0                     Brest    48.383     -4.495   
33        1 1840-12-31     NaN                     Brest    48.383     -4.495   
34        1 1841-12-31     NaN                     Brest    48.383     -4.495   
35        1 1842-12-31     NaN                     Brest    48.383     -4.495   
36        1 1843-12-31     NaN                     Brest    48.383     -4.495   
37        1 1844-12-31     NaN                     Brest    48.383     -4.495   
38        1 1845-12-31     NaN                     Brest    48.383     -4.495   
39        1 1846-12-31  6970.0                     Brest    48.383     -4.495   
40        1 1847-12-31  6956.0                     Brest    48.383     -4.495   
41        1 1848-12-31  6962.0                     Brest    48.383     -4.495   
42        1 1849-12-31  6959.0                     Brest    48.383     -4.495   
43        1 1850-12-31  6951.0                     Brest    48.383     -4.495   
44        1 1851-12-31  6939.0                     Brest    48.383     -4.495   
45        1 1852-12-31  6947.0                     Brest    48.383     -4.495   
46        1 1853-12-31  6947.0                     Brest    48.383     -4.495   
47        1 1854-12-31  6933.0                     Brest    48.383     -4.495   
48        1 1855-12-31  6936.0          

In [45]:
#function to use first tide measurement as zero reference point

def to_zero(dataframe):
    first_value = dataframe['tide'].iloc[0]
    dataframe['tide'] = dataframe['tide'] - first_value
    return dataframe

In [46]:
data_subset_viz = data_subset_viz.groupby(['ID']).apply(to_zero)

#### get top ten data

In [33]:
data_strongest_rise = data_subset_viz[(data_subset_viz['year'] == 2015)]

In [42]:
data_strongest_rise = data_strongest_rise.sort_values('tide', ascending=False)

In [43]:
data_strongest_rise.to_csv('top_ten_landrise.csv')

#### Convert year to object to get rid of 1985.0

In [47]:
data_subset_viz['year'] = data_subset_viz['year'].astype(object)

data_subset_viz.dtypes

ID                    int64
timestamp    datetime64[ns]
tide                float64
location             object
latitude            float64
longitude           float64
country              object
year                 object
dtype: object

In [48]:
## Add continent data

data_subset_viz = data_subset_viz.merge(continents, left_on='country', right_on='iso3')

In [49]:
data_subset_viz = data_subset_viz.drop('iso3', 1)

In [50]:
#data_subset_viz.to_csv('sealevel_viz_psmsl_1985_2015.csv')

data_subset_viz.to_csv('sealevel_viz_whole_timeseries.csv')

In [51]:
tidedata_series = (data_subset_viz.groupby(['ID'])
       .apply(lambda x: x[['year','tide']].to_dict('r'))
       .rename(columns={0:'tideData'}))
tidedata_series

ID
1       [{'year': 1807, 'tide': 0.0}, {'year': 1808, '...
3       [{'year': 1832, 'tide': 0.0}, {'year': 1833, '...
5       [{'year': 1938, 'tide': 0.0}, {'year': 1939, '...
7       [{'year': 1843, 'tide': 0.0}, {'year': 1844, '...
8       [{'year': 1848, 'tide': 0.0}, {'year': 1849, '...
9       [{'year': 1848, 'tide': 0.0}, {'year': 1849, '...
10      [{'year': 1854, 'tide': 0.0}, {'year': 1855, '...
11      [{'year': 1855, 'tide': 0.0}, {'year': 1856, '...
12      [{'year': 1856, 'tide': 0.0}, {'year': 1857, '...
14      [{'year': 1879, 'tide': 0.0}, {'year': 1880, '...
20      [{'year': 1862, 'tide': 0.0}, {'year': 1863, '...
22      [{'year': 1864, 'tide': 0.0}, {'year': 1865, '...
23      [{'year': 1865, 'tide': 0.0}, {'year': 1866, '...
24      [{'year': 1865, 'tide': 0.0}, {'year': 1866, '...
25      [{'year': 1865, 'tide': 0.0}, {'year': 1866, '...
32      [{'year': 1871, 'tide': 0.0}, {'year': 1872, '...
33      [{'year': 1872, 'tide': 0.0}, {'year': 1873, '...
41      [{'

In [52]:
cols = "ID location	latitude	longitude	country	continent".split()
j = data_subset_viz[cols].groupby("ID").first()
       #.to_json(orient='records', date_format='iso'))
j["tideData"] = tidedata_series
j = j.reset_index()
j = j.to_json(orient='records')

In [53]:
with open('data/subsets/dataexplorer.json', 'w') as fp:
    json.dump(json.loads(j), fp, indent=2, sort_keys=True)

print(json.dumps(json.loads(j), indent=2, sort_keys=True))

[
  {
    "ID": 1,
    "continent": "Europe",
    "country": "FRA",
    "latitude": 48.383,
    "location": "Brest",
    "longitude": -4.495,
    "tideData": [
      {
        "tide": 0.0,
        "year": 1807
      },
      {
        "tide": -51.0,
        "year": 1808
      },
      {
        "tide": -39.0,
        "year": 1809
      },
      {
        "tide": -35.0,
        "year": 1810
      },
      {
        "tide": -27.0,
        "year": 1811
      },
      {
        "tide": -26.0,
        "year": 1812
      },
      {
        "tide": -15.0,
        "year": 1813
      },
      {
        "tide": -17.0,
        "year": 1814
      },
      {
        "tide": -21.0,
        "year": 1815
      },
      {
        "tide": -25.0,
        "year": 1816
      },
      {
        "tide": -31.0,
        "year": 1817
      },
      {
        "tide": -23.0,
        "year": 1818
      },
      {
        "tide": -23.0,
        "year": 1819
      },
      {
        "tide": -26.0,
        "year": 18